In [ ]:
import numpy as np
import matplotlib.pyplot as plt
rand = np.random.random

### Classes and Functions

In [ ]:
def dist(x1, y1, x2, y2):
    return ((x1 - x2) ** 2 + (y1 - y2) ** 2) ** .5

def LJPotential(r, epsilon = 5, rm = 1.2):
    if r == 0:
        return 0
    else:
        f = epsilon * (((rm / r) ** 12) - 2 * ((rm / r) ** 6))
        if f > 500000:
            return 500000
        else:
            return f
    
def ODESolver(y, r, m):
    drdt = y[2:4]
    F = - LJPotential(r[0])
    theta = np.arctan2(r[2] - y[1], r[1] - y[0])
    Fx = F * np.cos(theta)
    Fy = F * np.sin(theta)
    ax, ay = Fx/m, Fy/m
    dvdt = [ax,ay]
    return np.concatenate((drdt, dvdt))

def find_closest(x1, y1, x2, y2, nx, ny):
    distances = []
    for i in [-nx, 0, nx]:
        for j in [-ny, 0, ny]:
            r = dist(x1, y1, x2 + i, y2 + j)
            distances.append((r, x2 + i, y2 + j))
    return min(distances, key=lambda x: x[0])

In [ ]:
class Particle:
    
    def __init__(self, system, x=0, y=0, vy=0, vx=0, mass=1):
        self.x = x
        self.y = y
        self.vx = vx
        self.vy = vy
        self.mass = mass
        self.system = system
        system.particles.append(self)
    
    def move(self, dt):
        """Moves the particle based on the current velocity, 
        and then changes the velocities based on the forces in the system"""
        
        y = np.array([self.x, self.y, self.vx, self.vy])
        dy = np.array([0,0,0,0])
        
        for p in self.system.particles:
            if p == self:
                continue
            else:
                r = np.array(find_closest(self.x, self.y, p.x, p.y, self.system.x_size, self.system.y_size))
                F1 = ODESolver(y, r, self.mass)
                F2 = ODESolver(y + ((dt/2) * F1), r, self.mass)
                F3 = ODESolver(y + ((dt/2) * F2), r, self.mass)
                F4 = ODESolver(y + (dt * F3), r, self.mass)
                dy = dy + ((dt / 6) * (F1 + (2 * F2) + (2 * F2) + F4))
          
        self.x = (self.x + (dy[0]/(len(self.system.particles)))) % self.system.x_size
        self.y = (self.y + (dy[1]/(len(self.system.particles)))) % self.system.y_size
        self.vx += dy[2]
        self.vy += dy[3]
                     
    def __repr__(self):
        return 'Particle:' + str([self.x, self.y])

In [ ]:
class System:
    
    def __init__(self, x_size, y_size):
        self.particles = []
        self.x_size = x_size
        self.y_size = y_size
        
    @property
    def x_vals(self):
        return [b.x for b in self.particles]
    
    @property
    def y_vals(self):
        return [b.y for b in self.particles]
    
    def move_all(self, dt):
        for p in self.particles:
            p.move(dt)
            
    @property
    def kinetic_energy(self):
        K = 0
        for p in self.particles:
            K += p.mass * p.vx ** 2
            K += p.mass * p.vy ** 2
        return K
            
    @property
    def potential_energy(self):
        P = 0
        for p1 in self.particles:
            for p2 in self.particles:
                r = find_closest(p1.x, p1.y, p2.x, p2.y, self.x_size, self.y_size)
                P += LJPotential(r)
        return .5 * P

### Simulation

In [ ]:
%matplotlib osx
nx, ny = 7, 7
sys = System(nx, ny)
sys2 = System(nx,ny)


# np.random.seed(51816)
for i in range(1,8):
    for j in range(1,9):
        theta = 2 * np.pi * rand()
        v = 2
        vxi = v * -np.sin(theta)
        vyi = v * np.cos(theta)
        if j % 2 == 0:
            Particle(system=sys, x=i + .5, y=j * .5 * (3 ** .5), vx=vxi, vy=vyi)
        else:
            Particle(system=sys, x=i, y= j * .5 * (3 ** .5), vx=vxi, vy=vyi)
            
for i in range(1,8):
    for j in range(1,8):
        theta = 2 * np.pi * rand()
        v = 100
        vxi = v * -np.sin(theta)
        vyi = v * np.cos(theta)
        if j % 2 == 0:
            Particle(system=sys2, x=i + .5, y=j * .5 * (3 ** .5), vx=vxi, vy=vyi)
        else:
            Particle(system=sys2, x=i, y= j * .5 * (3 ** .5), vx=vxi, vy=vyi)


fig = plt.figure(figsize=(14,7))
fig.suptitle('Noble Gas Particle Motion', fontsize = 24)
ax1 = fig.add_subplot(121)
ax2 = fig.add_subplot(122)

dt = .00001
i = 0
while True:
    sys.move_all(dt)
    sys2.move_all(dt)
    
    if i%10 == 0:
        ax1.clear()
        ax1.plot(sys.x_vals, sys.y_vals, 'o', ms=15)
        ax1.set_xlim((0,nx))
        ax1.set_ylim((0,ny))
        ax1.set_xlabel('x', fontsize = 16)
        ax1.set_ylabel('y', fontsize = 16)
        ax1.set_title('Low Temperature', fontsize=14)

        
        
        ax2.clear()
        ax2.plot(sys2.x_vals, sys2.y_vals, 'o', ms=15)
        ax2.set_xlim((0,nx))
        ax2.set_ylim((0,ny))
        ax2.set_xlabel('x', fontsize = 16)
        ax2.set_ylabel('y', fontsize = 16)
        ax2.set_title('High Temperature', fontsize=14)
        
#         plt.show()
#         plt.pause(.00001)
        plt.savefig('images/fig_{0:04}.png'.format(i//10))
        
    i += 1